In [191]:
import pandas as pd
import yaml

In [251]:
class node:

    def __init__(self):
        self.up = self
        self.down = self
        self.left = self
        self.right = self
        self.COL = None
        self.ROW = None

    def hideInCol(self):
        self.up.down = self.down
        self.down.up = self.up
        self.COL.row_count -= 1
        return self

    def showInCol(self):
        self.up.down = self
        self.down.up = self
        self.COL.row_count += 1
        return self

    def hideInRow(self):
        self.left.right = self.right
        self.right.left = self.left
        return self

    def showInRow(self):
        self.left.right = self
        self.right.left = self
        return self
    
    def deleteUnuseableRow(self):
        cur_cell = self.right 
        while cur_cell != self:
            print(cur_cell.COL.label)
            cur_cell.hideInCol()
            cur_cell = cur_cell.right
        print("done")
        self.hideInCol()
        return

    def hideWholeRow(self, start = None):
        if start == None: # if we just started the loop, don't hide me from my column, but go to my neighbor
            self.right.hideWholeRow(start = self)
            return
        if start != self: # we are not first and not last => hide me and continue
            self.hideInCol()
            self.right.hideWholeRow(start = start)
            return
        return # last possibility start == self => we have looped and can finish

    def showWholeRow(self, start = None):
        if start == None: # if we just started the loop, don't hide me from my column, but go to my neighbor
            self.left.showWholeRow(start = self)
            return
        if start != self: # we are not first and not last => hide me and continue
            self.showInCol()
            self.left.showWholeRow(start = start)
            return
        return # last possibility start == self => we have looped and can finish
    
    def getNeighbor(self, direction, by=0):
        neighbor = {
            'left'  : self.left,
            'right' : self.right,
            'up'    : self.up,
            'down'  : self.down
        }[direction]
        if by > 0:
            return neighbor.getNeighbor(direction, by = by-1)
        return neighbor




In [252]:
class columnHeader(node):

    def __init__(self, label):
        super().__init__()
        self.label = label
        self.row_count = 0
        self.COL = self

    def hideMe(self):
        self.hideInRow()
        cell = self.down
        while cell != self:
            cell.hideWholeRow()
            cell = cell.down
        return self

    def showMe(self):
        self.showInRow()
        cell = self.up
        while cell != self:
            cell.showWholeRow()
            cell = cell.up
        return self

    def appendRow(self, row):
        row.down = self
        row.up = self.up
        self.up.down = row
        self.up = row
        row.COL = self
        self.row_count += 1
        return self

    def addToRoot(self, root):
        root.appendColumn(self)
        return self

In [253]:
class rowHeader(node):
    
    def __init__(self, label):
        super().__init__()
        self.label = label
        self.ROW = self

    def appendColumn(self, col):
        col.right = self
        col.left = self.left
        self.left.right = col
        self.left = col
        col.ROW = self
        return self

    def addToRoot(self, root):
        root.appendRow(self)
        return self


In [254]:
class rootNode(columnHeader, rowHeader):

    def __init__(self):
        node.__init__(self)
        self.row_count = 0
        self.label = None
        self.ROW = self
        self.COL = self

    def addToRoot(self, root):
        pass

In [255]:
def append_dict(d, e):
    r = d.copy()
    r.update(e)
    return r

In [256]:
class einstein_matrix:
    
    def __init__(self, attributes):
        self.matrix_root = rootNode()

        self.column_headers = {
            atr_name : {
                atr_val : columnHeader(f"{atr_name} : {atr_val}").addToRoot(self.matrix_root)
                for atr_val in attributes[atr_name]
            }
            for atr_name in attributes
        }

        attr_names = list(attributes.keys())
        deg = len(attr_names)

        row_labels = [{}]
        for attr_name in attr_names:
            row_labels = [ append_dict(l, {attr_name : d_val})  for l in row_labels for d_val in attributes[attr_name]]

        self.row_headers = []

        # construct the sparse matrix

        for row_label in row_labels:

            row_header = rowHeader(row_label)
            self.matrix_root.appendRow(row_header)
        
            for attr_name in row_label:
                
                attr_val = row_label[attr_name]
                cell = node()
                row_header.appendColumn(cell)
                column_header = self.column_headers[attr_name][attr_val]
                column_header.appendRow(cell)

            self.row_headers.append(row_header)

    def remove_unusable_entires(self, facts):

        for fact in facts:
            
            (k1 , v1), (k2, v2) = fact.items()
            print(k1, v1, k2, v2)
            current_row = self.matrix_root.down

            while (current_row != self.matrix_root):
                label = current_row.label
                if (
                    label[k1] == v1 and label[k2] != v2 \
                    or label[k1] != v1 and label[k2] == v2 \
                ):
                    print(label)
                    current_row.deleteUnuseableRow()
                current_row = current_row.down


In [257]:
def search(matrix, solution=[], log=[], k=0):

    # print(f"k : {k}")

    if type(matrix) != rootNode:
        raise TypeError("Must start with matrix root node")

    # solution found if matrix is empty
    if matrix.right == matrix:
        print("ready")
        return prep_solution(solution)

    # select column
    col = matrix.right
    tmp_col = col
    while tmp_col != matrix:
        if tmp_col.row_count < col.row_count:
            col = tmp_col
        tmp_col = tmp_col.right
    print(col.label)
    # hide column 
    col.hideMe()
    # go through its each row
    row = col.down
    print(row.ROW.label)
    while row != col:
        # add row to solution
        solution.append(row)
        log.append(f"select R{row.ROW.label['R']}C{row.ROW.label['C']}={row.ROW.label['#']}")
        # hide row's columns
        cell = row.right
        while cell != row:
            if type(cell) != rowHeader:
                cell.COL.hideMe()
            cell = cell.right
        # go deeper
        result = search(matrix, solution, log, k = k+1)
        if result != None:
            return result
        # uncover columns and remove row from solution
        solution.pop()
        log.append("back")
        cell = row.left
        while cell != row:
            if type(cell) != rowHeader:
                cell.COL.showMe()
            cell = cell.left
        # next row
        row = row.down
    # # uncover column
    col.showMe()
    return None

    

In [258]:
filename = 'input_1_einstein.yml'

In [259]:
with open(filename, 'r') as f:
    riddle_text = yaml.safe_load(f)

In [260]:
m = einstein_matrix(riddle_text['attributes'])

In [261]:
m.remove_unusable_entires(riddle_text['facts'])

nationality Englishman color red
{'house_no': 1, 'color': 'red', 'nationality': 'Spaniard', 'drink': 'coffee', 'pet': 'dog', 'cigarettes': 'Old Gold'}
house_no : 1
color : red
nationality : Spaniard
drink : coffee
pet : dog
cigarettes : Old Gold
done
{'house_no': 1, 'color': 'red', 'nationality': 'Spaniard', 'drink': 'coffee', 'pet': 'dog', 'cigarettes': 'Kools'}
house_no : 1
color : red
nationality : Spaniard
drink : coffee
pet : dog
cigarettes : Kools
done
{'house_no': 1, 'color': 'red', 'nationality': 'Spaniard', 'drink': 'coffee', 'pet': 'dog', 'cigarettes': 'Chesterfields'}
house_no : 1
color : red
nationality : Spaniard
drink : coffee
pet : dog
cigarettes : Chesterfields
done
{'house_no': 1, 'color': 'red', 'nationality': 'Spaniard', 'drink': 'coffee', 'pet': 'dog', 'cigarettes': 'Lucky Strike'}
house_no : 1
color : red
nationality : Spaniard
drink : coffee
pet : dog
cigarettes : Lucky Strike
done
{'house_no': 1, 'color': 'red', 'nationality': 'Spaniard', 'drink': 'coffee', 'pet'

In [271]:
r = m.matrix_root
s = r.right
while (s != r):
    if s.row_count <1 :
        print(s.label)
    s = s.right